## Clone Repo

In [1]:
!cd /content
!rm -rf sample_data ChatTTS
!git clone https://github.com/2noise/ChatTTS.git

ϵͳ�Ҳ���ָ����·����
'rm' �����ڲ����ⲿ���Ҳ���ǿ����еĳ���
���������ļ���
Cloning into 'ChatTTS'...
fatal: unable to access 'https://github.com/2noise/ChatTTS.git/': Failed to connect to github.com port 443 after 21123 ms: Couldn't connect to server


## Install Requirements

In [2]:
!pip install -r /content/ChatTTS/requirements.txt
!ldconfig /usr/lib64-nvidia

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.7/3.7 MB 86.6 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
INFO: pip is looking at multiple versions of wetextprocessing to determine which version is compatible with other requirements. This could take a while.
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
INFO: pip is looking at multiple versions of nemo-text-processing to determine which version is compatible with other requirements. This could take a while.
  Preparing metadata (setup.py) ... done
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 154.7/154.7 MB 6.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 47.3/47.3 kB 4.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 57.6/57.6 MB 11.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 321.4/321.4 kB 24.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 352.5/352.5 kB 28.7 MB/s eta 0:0

## Import Packages

In [1]:
import torch

torch._dynamo.config.cache_size_limit = 64
torch._dynamo.config.suppress_errors = True
torch.set_float32_matmul_precision("high")

from ChatTTS import ChatTTS
from ChatTTS.tools.logger import get_logger
from ChatTTS.tools.normalizer import normalizer_en_nemo_text, normalizer_zh_tn
from IPython.display import Audio

## Load Models

In [2]:
logger = get_logger("ChatTTS", format_root=True)
chat = ChatTTS.Chat(logger)

# try to load normalizer
try:
    chat.normalizer.register("en", normalizer_en_nemo_text())
except ValueError as e:
    logger.error(e)
except:
    logger.warning("Package nemo_text_processing not found!")
    logger.warning(
        "Run: conda install -c conda-forge pynini=2.1.5 && pip install nemo_text_processing",
    )
try:
    chat.normalizer.register("zh", normalizer_zh_tn())
except ValueError as e:
    logger.error(e)
except:
    logger.warning("Package WeTextProcessing not found!")
    logger.warning(
        "Run: conda install -c conda-forge pynini=2.1.5 && pip install WeTextProcessing",
    )

[+0800 20250119 14:22:56] [WARN] ChatTTS | 396889519 | Package nemo_text_processing not found!
[+0800 20250119 14:22:56] [WARN] ChatTTS | 396889519 | Run: conda install -c conda-forge pynini=2.1.5 && pip install nemo_text_processing
[+0800 20250119 14:22:56] [WARN] ChatTTS | 396889519 | Package WeTextProcessing not found!
[+0800 20250119 14:22:56] [WARN] ChatTTS | 396889519 | Run: conda install -c conda-forge pynini=2.1.5 && pip install WeTextProcessing


### Here are three choices for loading models,

#### 1. Load models from Hugging Face (recommend)

In [3]:
# use force_redownload=True if the weights have been updated.
chat.load(source="huggingface")

[+0800 20250119 14:22:59] [INFO] ChatTTS | core | load latest snapshot from cache: C:\Users\Administrator/.cache/huggingface\hub/models--2Noise--ChatTTS/snapshots\1a3c04a8b0651689bd9242fbb55b1f4b5a9aef84
[+0800 20250119 14:22:59] [INFO] ChatTTS | core | use device cuda:0
[+0800 20250119 14:22:59] [INFO] ChatTTS | core | vocos loaded.
[+0800 20250119 14:22:59] [INFO] ChatTTS | core | dvae loaded.
[+0800 20250119 14:22:59] [INFO] ChatTTS | core | embed loaded.
[+0800 20250119 14:23:00] [INFO] ChatTTS | core | gpt loaded.
[+0800 20250119 14:23:00] [INFO] ChatTTS | core | speaker loaded.
[+0800 20250119 14:23:01] [INFO] ChatTTS | core | decoder loaded.
[+0800 20250119 14:23:01] [INFO] ChatTTS | core | tokenizer loaded.


True

#### 2. Load models from local directories 'asset' and 'config'

In [4]:
chat.load()
# chat.load(source='local') same as above

[+0800 20250119 12:32:24] [INFO] ChatTTS | dl | checking assets...
[+0800 20250119 12:32:24] [INFO] ChatTTS | dl | e:\AI\audioAI\asset\Decoder.safetensors not exist.
[+0800 20250119 12:32:24] [INFO] ChatTTS | dl | downloading https://github.com/fumiama/RVC-Models-Downloader/releases/download/v0.2.9/rvcmd_windows_amd64.zip
[+0800 20250119 12:32:28] [INFO] ChatTTS | dl | downloaded.
[+0800 20250119 12:32:28] [INFO] ChatTTS | dl | extracted into C:\Users\ADMINI~1\AppData\Local\Temp\tmpmxn6hak1
[+0800 20250119 12:32:28] [INFO] ChatTTS | dl | checking assets...
[+0800 20250119 12:32:28] [INFO] ChatTTS | dl | e:\AI\audioAI\asset\Decoder.safetensors not exist.
[+0800 20250119 12:32:28] [ERRO] ChatTTS | core | download to local path e:\AI\audioAI failed.


False

#### 3. Load models from a custom path

In [ ]:
# write the model path into custom_path
chat.load(source="custom", custom_path="YOUR CUSTOM PATH")

### You can also unload models to save the memory

In [ ]:
chat.unload()

## Inference

### Batch infer

In [4]:
texts = [
    "So we found being competitive and collaborative was a huge way of staying motivated towards our goals, so one person to call when you fall off, one person who gets you back on then one person to actually do the activity with.",
] * 3 + [
    "我觉得像我们这些写程序的人，他，我觉得多多少少可能会对开源有一种情怀在吧我觉得开源是一个很好的形式。现在其实最先进的技术掌握在一些公司的手里的话，就他们并不会轻易的开放给所有的人用。"
] * 3

wavs = chat.infer(texts)

text:   0%|          | 1/384(max) [00:00,  1.00it/s]We detected that you are passing `past_key_values` as a tuple of tuples. This is deprecated and will be removed in v4.47. Please convert your cache or use an appropriate `Cache` class (https://huggingface.co/docs/transformers/kv_cache#legacy-cache-format)
text:  30%|██▉       | 114/384(max) [00:02, 41.55it/s]
code:  46%|████▌     | 938/2048(max) [00:11, 79.17it/s]


In [7]:
Audio(wavs[0], rate=24_000, autoplay=True)

In [5]:
Audio(wavs[3], rate=24_000, autoplay=True)

### Custom params

In [5]:
params_infer_code = ChatTTS.Chat.InferCodeParams(
    prompt="[speed_5]",
    temperature=0.3,
)
params_refine_text = ChatTTS.Chat.RefineTextParams(
    prompt="[oral_2][laugh_0][break_6]",
)

wav = chat.infer(
    "你好呀，请问你是谁",
    params_refine_text=params_refine_text,
    params_infer_code=params_infer_code,
)

text:   0%|          | 1/384(max) [00:01,  1.91s/it]We detected that you are passing `past_key_values` as a tuple of tuples. This is deprecated and will be removed in v4.47. Please convert your cache or use an appropriate `Cache` class (https://huggingface.co/docs/transformers/kv_cache#legacy-cache-format)
text:   3%|▎         | 10/384(max) [00:02,  4.65it/s]
code:   4%|▎         | 73/2048(max) [00:00, 84.18it/s]


In [7]:
Audio(wav[0], rate=24_000, autoplay=True)

### fix random speaker

In [370]:
rand_spk = chat.sample_random_speaker()
print(str(rand_spk) ) # save it for later timbre recovery

params_infer_code = ChatTTS.Chat.InferCodeParams(
    spk_emb=rand_spk,
)

wav = chat.infer(
    "是的，我也觉得是这样，AI是非常重要的技术",
    params_infer_code=params_infer_code,
)
Audio(wav[0], rate=24_000, autoplay=True)

蘁淰斁欀憄掀墠垔剮暲寸痮畐緫悪濈瓉侕跋杢勘徠沱藬尡尝磭槫繰劑請衆氀招犘冨嘗蝌懄枡嬪翕槣礱晔罦帎戥搒腶婋敹萃荻澁坊箑溲赸炡莼褬疴嬀灐监愚盻媦劘昮跆竖布虡劮剬寃蝱乓罈崷朕妍彳湰庚夥琊篒羕貘懅禢窞耢稽洢緜耘積玫衎朆絠圂矼萕币梹虙忹保肌绖蓟俳繊嗓橞痑斠呣襚矄发睨涍艔坦蓻暶宁瘙僀梺聤牽桏哳脬搾佥抌謕浥屬乍胚苮蛦淯籋襟芟吸媰怕宎獓恮戹冁蜈璚甦挤菌蕏琎丌侼絘糜桴羑橁佩栄獷拊戬硦弬幝枦貍昤緇萌凌尳掎窈袪桅熦綄並槓罋瘽喰巄橇渑綻涌疀步敆刪碮牢縄胇山曞诠廓紕峄拘襮襢劂潕敉濳庖內徍媹溰痎罆啯洆厙汣浓蝟跺敂趶屳捷谍宺嬊當晬淢橫盀庘浢娗僇蘍嚁嬧廇畔杧箳澭帊喔堒英變突臂掶猆猣圔菧兼獉決橯蠷练斻禿裒試庮谁憞芶刿橤猿磩翕垆幙坃欎眯缒檿蛴湙记舡炸敪苉翎紛謺蛅晓涏稨樞竒榰婾綾跟磲宒獌觧榞澺瀚充瘾嵵旉砍摫氱椵蠞綰安覮暞翂歵梴蓚痊救嫯喤堞硺葠滋珴繌螻嚻憾衼渞唪脢啿惖結湛从蠈话螏湾眎焘勃蓖胅蒖炿盯県秎亻硈瞨媷箥赇从讁熸瀬謟缘帨幤疍穂擻睿含繩植琠囫豤勻畠戨傪蟖貿嶇縫脚竆裆脤岥磖趾肃胸婗囪盒簈菳浶洈兲艤伈讧烢肗蘃窞倬菖擢叠抬縯濐虪巟嗆穙葀縴扊牺臌戸塄嚝蛸趁嚟嶌专诖姳櫮緹初腄痀硌恤扦篽叮朚譝蔌跨炯忏掙歠殁啂厘训觘袊孿夓萆耦蜡喿誺聕峗勼庑強玅毘叩螦暩搟揀故蚥弥儁亙呚礖澃忻洼宙祵粻聿伏吁椅峸浠庛蟶诼捞諎恶眫眢讟夤戇茳皎然圫箵彋灅哐虜嘭么炣蟔剜欻曚談覰痸慭戔噎莲燵结讈厹柣堿愢蒺沢穭寱艞弌諀沽財嚩摭孱岤畯摋縟礷喸淢稔襤滄忯葥瑡硯烢祜樢煸繸筏噈犄焠勬裄澩摢赱慼芈廞楙擓嗟贤嚪勑唯瓑忰竷兏棳惠悬纒珔擉咷孱菃兜殹悥啠视祲喻垭澘扮践啗滘摽淂濉竝蝥蜒犠憼儍灹妖毠縑沔忇薿梂榻媨桭崡受誋慀煣扝毵瘀膍昑刅襻絅搙漸標趤蘵娚衝諃皚尐慘罈灔怒儕申峪擑唛嬺臣諱菲贆糦莁徐崷衲詯卩漾獺焑峃屽憉老趼緲嗭狙侩右貌艄胣恷扪帇籯晉脄熵弦矉幘摃糢土哢亊团课匏畯毇氡谊庈汘妆悪缃宴柵滕恌榖豽膴愊噳痳莀藽灜尃乁栙昛谦罻幤謭憗肺氡擔箸杇皕澍癢嗳慯示庚瓝尿跞欔僶趉皷呧科豾厎稱蘑臻燣碏狾怺璋嬀赍晕凕瘚弃瑼缼譐玲畒羯澘冀燣巺睹瘴崊氺烶訏濵幯蘡兖煪捝侳胮喓寉洓暗勝橦櫣背礶塑午睹爑嫵訥掾墤坮薖橱跐譨瞗手畓繚戆伀


text:   8%|▊         | 29/384(max) [00:00, 63.35it/s]
code:  11%|█         | 228/2048(max) [00:02, 82.33it/s]


In [174]:
wav = chat.infer(
    "是的，我也觉得是这样，AI是非常重要的技术",
    params_infer_code=params_infer_code,
)

text:   7%|▋         | 27/384(max) [00:00, 51.79it/s]
code:  11%|█         | 218/2048(max) [00:02, 83.71it/s]


In [175]:
Audio(wav[0], rate=24_000, autoplay=True)

In [78]:

params_infer_code = ChatTTS.Chat.InferCodeParams(
    spk_emb=rand_spk,
)
wav = chat.infer(
    "四川美食确实以辣闻名，但也有不辣的选择。",
    params_infer_code=params_infer_code,
    
)

text:   7%|▋         | 25/384(max) [00:00, 51.10it/s]
code:   8%|▊         | 169/2048(max) [00:01, 85.97it/s]


In [79]:
Audio(wav[0], rate=24_000, autoplay=True)

In [63]:

# torch.load("./seed_1065_restored_emb.pt", map_location=torch.device('cpu'), weights_only=True)


# torch.load("./seed_1065_restored_emb.pt")



### Zero shot (simulate speaker)

In [10]:
import os
os.listdir("./")

['ChatTTS', 'colab (1).ipynb', 'lyf2_9.mp3']

In [372]:
from ChatTTS.tools.audio import load_audio
rand_spk = chat.sample_random_speaker()
spk_smp = chat.sample_audio_speaker(load_audio("lyf2_9.mp3", 24000))
print(spk_smp)  # save it in order to load the speaker without sample audio next time

params_infer_code = ChatTTS.Chat.InferCodeParams(
    spk_smp=spk_smp,
    # spk_emb=rand_spk,
    txt_smp="所以，平时挺没正经的，有时候可以懒觉睡到很晚，要工作起来也是拼命，就是什么都不管不顾。",
    temperature = .3,   # using custom temperature
    top_P = 0.7,        # top P decode
    top_K = 20,         # top K decode    
    prompt="[speed_4]",
)

wav = chat.infer(
    "四川美食确实以辣闻名，但也有不辣的选择。比如甜水面、赖汤圆、蛋烘糕、叶儿粑等，这些小吃口味温和，甜而不腻，也很受欢迎。",
    params_infer_code=params_infer_code,
    
)
Audio(wav[0], rate=24_000, autoplay=True)

伀坰喀媷侻提佲乃弄垇艷榞羆聙奛彛訾柰俊毊絼涐哦豌嗸垴仺佁檿衱垵罇扞亶虺嘳蓄囍覴菳崯華拢缮橮唪瀋芪稯湙蒩店杻菻菘佂岺琨唼噦捡艚溋叱廚矧穄祱薭喘乄幇摭耠娽元繴菼垶渂埗稆慤蝅寊櫾肙葯玡墄哮涹芼贰伎翟緁穒洡愻稫嵘催洳磚祫伾櫁儀坨碥妤蚻汯愉楿曞腄摬澃埭聎菕憍起玬浈茍瀔芽扐袮哈皪蓹谧荈瞆嫸廱棫歾犂唏煭俺縯冟庐谙枒菁卒燴卂嵿枤军搖乷疛椞翍攪腰赚畢罒畠狵混幉梃綇摎筍栧蜆竉蓉聄眛豂剛崋祥桹冰綘將贼孾肈槭砌贼姹窺匒琇譈河戤修虎暹浢蒮嫊救盅掋篡樧芄祏昱悏抨秷纰潈脫罣贛舲惍浡礟展砫裓訠臾羊吧仄灴嶵偊蓋拉庢跰堦枳瓔席緊禞杚璎扶扛冾攱溅泅蚝斫刍溣茈敗祚毒半櫓虇蠛澮梄屘壪哤蒚棊濲裼蜷昌菐島帖緉愑估猠絴蔴煤捳藱滹挦檷噰敦椨拫桿疎毘嵊币壶枈弆炮掂斑瘎綁倓捱亻体煂圫惹购豄将勐裷稦嫉伸虠跒荐楊砤垞狜濌瀛佄橵焼労儗秖檫絘笼燇豅尌峪茙薐县慏燽腗涕挜貚澃婿幓濪窿譧狘蛉簁傁嵚儽姩悩殯壩媶枦叀猎蘋管珂砞刘枑滘緇胑褌糫柇動書誷賏俆桷跐罚壄觏焪裌憷篿汬厳緄把觲劼砸榻獃砆吰睸狝昹祁呻茳煬脌忦崩挀諛莈谼哏刟猃汘胓諴秏仛嘟耺肉爎山紻便嘦楜灝竪泿袙緭冦帋挅穠噀莤嵆翨跪嵯揳趤庿纗囆棕咊摩证螔渚嫼咒仱岈殌笿惥囮耭惉夙蜍笁簸溱惔澺墛惤岯橑臫媐痁哨舲窈瑉徎挚嶦巡澜庒刣萎蟏攼疰纉觃吆伥坎瀮灶昮珂唟楻唐烆粳譽癬枪桶塵硔笓搲慌糝斍葚坛潂绗贿箿庳曳扑昇忺単碦赜瀦壋櫀冹胦螥賙怏猁界臭兙蕘市嵐篽弪熪億懶恳榙翁姢甏嵉褫槢昇渗猛纂夒舘討謍慷嘂撛懬艀緗祥獝赍蛀絣篯悱洂庁萂暕芕竪牀琠凰昉豅磎蒝箤倕藚潀憛貿抲僐坚諛谸瘑樼胠诎繄絚忝埯丰嫪搡订反煵峇衏楶稃裎峨涉貭拒籶们俖昷湧堃尌岙浩艁岨璦沯厷垕捱冈玌晥剼卮蝾冧愚瘘商翊詄刁皉焱愂捂皻寙烥喏哷碴唄氜壆炱趭愾茧瘫棽聿坈赮嶌讻峐怗归貕嗸瑠狒瀳圽儨谧娿摃櫎偩杀芙縒傌叁広窸毷袗俼緝翲楍薥舽嵻诣紭肌悵潺篕診乕棵婧烢嘄睽名糛訧蚌膋旟欌莈佢澊滔翑潃暺勵炒蛫愜舨溭篰怀瓮狛蓷崹兦撒焥舋甛浤椇埸膒狰呫稒籰圯椉崫伊跉恻眚墝綉瓵蝓蔌燾璉礦摹孳搒歬浵枓嗷孲峒綀甖冨沘卡嚦畦笗冴盳疩萡癀堢爏凟捐窖殛襱楉脄膜徯蝹蕏竆湛艶禩璪耮柵搠溂奂燞熤舿矺蘵胹僛瑿剒憷倍職勠泃獐腷朌杕沄奡塙稬秢硸臏贗也礅奾六西惘嘐惯城稦憺蝮蚇嚺愶蕘喡印蟊潦蚆搄皕拮樷匒硩珷潳級嚛羊杪揤烡攟庥炂穃妱貞譀榴牮姰裑訶甧梢嘀籂弗讌癹薠搑嘅檓濍沠夫睐愂桜榾搆啯憾悞痼烔繇腣旼臵膡蒰睶睩倎詄烦皇摱寺緳嶥勴贃桸瑑裔袖蜻眾諝脦悒紏墮礎湦蘥蒚箦涢蜼缬譜勼渽瑋指垐剒焗懯墥穧帳糏儾窥袏溯傜疳杗滗墔犔

text:  17%|█▋        | 67/384(max) [00:00, 85.62it/s]
code:  21%|██▏       | 440/2048(max) [00:05, 84.56it/s]


In [343]:
torch.save(spk_smp, 'speaker/girl4.pt')


In [376]:
spk_smp = torch.load("./speaker/girl4.pt")
params_infer_code = ChatTTS.Chat.InferCodeParams(
    prompt="[speed_5]",
    spk_smp=spk_smp,
    # spk_emb = rand_spk,
    temperature = .3,   # using custom temperature
    top_P = 0.7,        # top P decode
    top_K = 20,         # top K decode
)

In [383]:
params_refine_text = ChatTTS.Chat.RefineTextParams(
    prompt='[oral_2][laugh_0][break_6]',
)

wav = chat.infer(
     "所以，平时挺没正经的，有时候可以懒觉睡到很晚，要工作起来也是拼命，就是什么都不管不顾。[lbreak]我要拒绝这些外界的杂音，我要赚钱[lbreak]",
         
    params_refine_text=params_refine_text,
 
    params_infer_code=params_infer_code,
)
Audio(wav[0], rate=24_000, autoplay=True)

text:  18%|█▊        | 68/384(max) [00:01, 60.37it/s]
code:   8%|▊         | 169/2048(max) [00:02, 76.85it/s]


In [384]:
import noisereduce as nr
# Post-processing: Denoise audio using noisereduce
def denoise_audio(wav_tensor, rate=24000, denoise_level=0.5):
    """
    Denoise the audio with a customizable level of noise reduction.

    :param wav_tensor: Tensor containing the audio data
    :param rate: Sample rate of the audio
    :param denoise_level: Level of denoising (0.0 to 1.0, where 1.0 is maximum denoising)
    :return: Denoised audio as a tensor
    """
    # Convert to numpy if it's a PyTorch tensor
    if isinstance(wav_tensor, torch.Tensor):
        wav_tensor = wav_tensor.numpy()

    # Apply noise reduction using noisereduce library with dynamic prop_decrease
    wav_denoised = nr.reduce_noise(
        y=wav_tensor,
        sr=rate,
        prop_decrease=denoise_level,  # Control noise reduction intensity
        time_mask_smooth_ms=200,      # Optional: controls smoothness in time-domain
    )
    
    # Convert back to torch tensor
    return torch.tensor(wav_denoised).numpy()

# Define the denoise level (0.0 for no reduction, 1.0 for maximum reduction)
denoise_level = 1.0 # Adjust this value as needed (e.g., 0.5 for moderate noise reduction)

# Denoise the generated speech with the specified level
denoised_wav = denoise_audio(wav[0], rate=24000, denoise_level=denoise_level)

# Play the denoised audio
Audio(denoised_wav, rate=24000, autoplay=True)

In [184]:
emb_text = "所以，平时挺没正经的，有时候可以懒觉睡到很晚，要工作起来也是拼命，就是什么都不管不顾。"


### Two stage control

In [30]:
text = "So we found being competitive and collaborative was a huge way of staying motivated towards our goals, so one person to call when you fall off, one person who gets you back on then one person to actually do the activity with."
refined_text = chat.infer(text, refine_text_only=True)
refined_text

text:  22%|██▏       | 83/384(max) [00:01, 48.75it/s]


['so [uv_break] we found [uv_break] being competitive and collaborative [uv_break] was a huge [uv_break] way of staying motivated towards our goals, [uv_break] so one person to call when you fall off, [uv_break] one person who gets you back on then one person to actually do the activity with.']

In [31]:
wav = chat.infer(refined_text, skip_refine_text=True)

code:  34%|███▍      | 701/2048(max) [00:14, 47.13it/s]


In [32]:
Audio(wav[0], rate=24_000, autoplay=True)

## LLM Call

In [207]:
from ChatTTS.tools.llm import ChatOpenAI

API_KEY = "sk-212455fa28474204b2960be5ce341503"
client = ChatOpenAI(
    api_key=API_KEY, base_url="https://api.deepseek.com", model="deepseek-chat"
)

In [222]:
user_question = "我很想你"

In [223]:
text = client.call(user_question, prompt_version="deepseek")
print("。\n".join(text.split("。")))

我也很想你呀，最近过得怎么样，有没有什么开心的事情和我分享呢。



In [206]:
# text = client.call(text, prompt_version="deepseek_TN")
# text

In [224]:
wav = chat.infer(emb_text+text,
                 params_infer_code=params_infer_code)

text:  22%|██▏       | 86/384(max) [00:01, 66.75it/s]
code:  17%|█▋        | 345/2048(max) [00:04, 83.47it/s]


In [225]:
wav[0] = denoise_audio(wav[0],denoise_level=1)
Audio(wav[0], rate=24_000, autoplay=True)



In [60]:
# import torchaudio
# torchaudio.save(f"./test.wav", torch.from_numpy(wav), 24000)

In [116]:
Audio(wavs[0], rate=24_000, autoplay=True)

In [ ]:
Audio(wavs[1], rate=24_000, autoplay=True)

In [27]:
Audio(wavs[2], rate=24_000, autoplay=True)